In [23]:
import numpy as np
import random

In [24]:
n_samples = 500
start_limit = 0.1
end_limit = 6.9
memory_length = 5
step = (end_limit-start_limit)/(n_samples-1)

In [25]:
target = np.linspace(start_limit, end_limit, num=n_samples)
#np.random.shuffle(target)

In [26]:
features = np.zeros((n_samples, memory_length))
for i in range(features.shape[1]):
    features[:,i] = target + ((i+1)*step)

In [27]:
features = np.sin(features)
target = np.sin(target)

In [28]:
def get_reward(goal, action):
    action = action - 0.5
    # right action
    if goal * action > 0:
        return 1.0
    # wrong action
    else:
        return -1.0

In [29]:
def eval_model(model, features, target):
    preds = model.predict(features)
    decision = np.argmax(preds, axis=1)
    
    goal = np.zeros(target.shape)
    
    goal[features[:,0] < target] = 1
    goal[features[:,0] > target] = 0
    print('goal, decision')
    print(goal, decision)
    
    return f'{(1-np.mean(np.abs(goal-decision)))*100}%', goal, decision

In [30]:
# neuralis halo felepitese
from keras.models import Sequential
from keras.layers.core import Dense, Dropout, Activation
from keras.optimizers import RMSprop

In [31]:
model = Sequential()
model.add(Dense(25, kernel_initializer='lecun_uniform', input_shape=(memory_length,)))
model.add(Activation('relu'))
#model.add(Dropout(0.2))

model.add(Dense(50, kernel_initializer='lecun_uniform'))
model.add(Activation('relu'))
#model.add(Dropout(0.2))

model.add(Dense(25, kernel_initializer='lecun_uniform'))
model.add(Activation('relu'))
#model.add(Dropout(0.2))

model.add(Dense(2, kernel_initializer='lecun_uniform'))
model.add(Activation('linear')) #linear output so we can have range of real-valued outputs

rms = RMSprop()
model.compile(loss='mse', optimizer=rms)

In [32]:
epochs = 45000
epsilon = 1


In [33]:
for i in range(epochs):
    j = np.random.choice(n_samples, 1)
    x = features[j]

    qval = model.predict(x, batch_size=1)
    if (random.random() < epsilon): #choose random action
        action = np.random.randint(0,2)
    else: #choose best action from Q(s,a) values
        action = (np.argmax(qval))

    # move to next state (there's no)
    # calc next Q values
    # newQ = model.predict(new_state, batch_size=1)
    reward = get_reward(target[j]-features[j,0], action)
    
    y = np.zeros(2)
    y[:] = qval[:]
    # set update value, but it's definitely terminal state
    # so update is this simple
    update = reward
    y[action] = update
    y = y.reshape(1,2)
    model.fit(x, y, batch_size=1, epochs=1, verbose=1)
    
    # reduce epsilon value
    if epsilon > 0.1:
        epsilon -= (1/epochs)*5
    

Epoch 1/1
1/1 [==============================] - 0s 142ms/step - loss: 0.2648
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5706
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4999
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4225
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5616
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.9003
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4385
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.6420
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.2553
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.4632
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4177
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.7220
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4281
Epoch 1/1


Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.1687
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4575
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5282
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5852
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5257
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4855
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.2519
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5122
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.2222
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4826
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5099
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5138
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4821
Epoch 1/1
1/

Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4543
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.1286
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.4039
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.8946
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.2968
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.6731
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.8983
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.3131
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.9017
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.3502
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.9354
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.1776
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.2645
Epoch 1/1
1/

Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5201
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.5485
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5526
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.3122
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4953
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4915
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.1277
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.3846
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 1.7730
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4570
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.2295
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5766
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.3429
Epoch 1/1
1/

Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.3487
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.5579
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.3824
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.3062
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4206
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.7588
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.7929
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.7306
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.5448
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.3670
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.3603
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.4617
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.2937
Epoch 1/1
1/

...

Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0051
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0011
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0243
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0876
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 3.6934e-04
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.8698
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 9.9418e-04
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.9452
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0850
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 8.7382e-05
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0047
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0132
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0042


Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0230
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 2.1099e-05
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0090
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 1.9085e-04
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.0059
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 2.9215e-04
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0127
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.1645
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 8.4719e-04
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 7.2692e-04
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0089
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 1.5528e-04
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - l

Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0052
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0013
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.1285
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 9.5653e-04
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0669
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0035
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0045
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0017
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0023
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.9897
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0011
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0436
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0388
Epoch 1/

Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0055
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0016
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0065
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0012
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.5382
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0178
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0047
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 1.3504e-06
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 2.1862e-06
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 4.9151e-06
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.1052
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0017
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0321


Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 8.8450e-04
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0859
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0063
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0520
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0161
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0052
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0052


In [34]:
prec, goal, decision = eval_model(model, features, target)

goal, decision
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.

In [35]:
prec

'97.2%'

In [19]:
prec

'92.80000000000001%'

In [22]:
prec

'93.39999999999999%'